Thoughts:

I had a theory: The model is incentivised to create a flat plane to minimize f(t,x). This way u, u_t, u_x, and u_xx are all close to 0. Additionally, since boundary points at x = = -1, 1 all have the same value (0), a flat plane wouldn't hurt either. It is the easiest way. This theory worked. Until I made all the data points the ones at t = 0 and completely took away the MSE_f loss component. Still, a flat plane appeared. Still, the derivatives died. Less than before. But given that the ONLY job of the entire network at this point was to approximate -sin(x*\pi), it is but a bit concerning that it is STILL unable to do that.


This notebook will get rid of all collocation point code and the MSE_f term. Just seeing if I can train to model to fit the dataset at all

Import statements

In [183]:
import os
import torch
import torchvision
from torch import nn 
from torch.autograd import Variable
from torchvision import transforms
from torch.utils.data import DataLoader
import torch.nn.functional as F
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import math
from torch.utils.data import Dataset
import pyDOE2
from torch.autograd.functional import jacobian, hessian


Variables

In [184]:
num_data_points = 200

Generating Data

In [185]:
'''num_points_t_0 = (int) (num_data_points * proportion_t_0)
num_points_x_1 = (num_data_points - num_points_t_0)//2 # // is integer division
num_points_x_neg_1 = num_data_points - num_points_t_0 - num_points_x_1

#create num_data_points random data points on the boundaries of the PDE
t_0_points = np.array( list( zip(np.zeros(num_points_t_0), 2 * np.random.rand(num_points_t_0) - 1 ) ) )
x_1_points = np.array( list( zip(np.random.rand(num_points_x_1), np.full(num_points_x_1, 1)) ) ) #np.full() takes paramters shape, value. Shape can be a tuple for multidimensional arrays filled with value.
x_neg_1_points = np.array( list( zip(np.random.rand(num_points_x_neg_1), np.full(num_points_x_neg_1, -1)) ) )
x_points = np.concatenate(( x_1_points, x_neg_1_points ))

#Generating labels with the data
dtype = [('points', float, 2), ('label', float)] #need custom dtype because otherwise numpy doesn't like these combined arrays

t_0_labels = -np.sin(np.pi * t_0_points[:,1] )
t_0_combined = np.array(list( zip(t_0_points, t_0_labels) ), dtype=dtype)

x_labels = np.zeros(num_points_x_1 + num_points_x_neg_1)
x_combined = np.array(list( zip(x_points, x_labels) ), dtype=dtype)

combined_labels_data = np.concatenate( (t_0_combined, x_combined) )

np.random.shuffle(combined_labels_data)

data_points, labels = map(np.array, map(list, zip(*combined_labels_data)) )'''


"num_points_t_0 = (int) (num_data_points * proportion_t_0)\nnum_points_x_1 = (num_data_points - num_points_t_0)//2 # // is integer division\nnum_points_x_neg_1 = num_data_points - num_points_t_0 - num_points_x_1\n\n#create num_data_points random data points on the boundaries of the PDE\nt_0_points = np.array( list( zip(np.zeros(num_points_t_0), 2 * np.random.rand(num_points_t_0) - 1 ) ) )\nx_1_points = np.array( list( zip(np.random.rand(num_points_x_1), np.full(num_points_x_1, 1)) ) ) #np.full() takes paramters shape, value. Shape can be a tuple for multidimensional arrays filled with value.\nx_neg_1_points = np.array( list( zip(np.random.rand(num_points_x_neg_1), np.full(num_points_x_neg_1, -1)) ) )\nx_points = np.concatenate(( x_1_points, x_neg_1_points ))\n\n#Generating labels with the data\ndtype = [('points', float, 2), ('label', float)] #need custom dtype because otherwise numpy doesn't like these combined arrays\n\nt_0_labels = -np.sin(np.pi * t_0_points[:,1] )\nt_0_combined = n

Data Validation Code

In [186]:
'''# Test 1: Ensure all data points lie on the correct boundaries
def test_boundaries(data_points):
    t_values = data_points[:, 0]
    x_values = data_points[:, 1]
    assert np.all((t_values == 0) | (x_values == 1) | (x_values == -1)), "Some points do not lie on the correct boundaries."

test_boundaries(data_points)
print("Test 1 passed!")

# Test 2: For t=0, label should be -sin(pi * x)
def test_labels_t_0(data_points, labels):
    mask_t_0 = data_points[:, 0] == 0
    expected_labels = -np.sin(np.pi * data_points[mask_t_0, 1])
    assert np.allclose(labels[mask_t_0], expected_labels), "Labels for t=0 do not match -sin(pi * x)."

test_labels_t_0(data_points, labels)
print("Test 2 passed!")

# Test 3: For x=-1 or x=1, label should be 0
def test_labels_x_boundaries(data_points, labels):
    mask_x_boundaries = (data_points[:, 1] == 1) | (data_points[:, 1] == -1)
    assert np.all(labels[mask_x_boundaries] == 0), "Labels for x=-1 or x=1 are not zero."

test_labels_x_boundaries(data_points, labels)
print("Test 3 passed!")
'''

'# Test 1: Ensure all data points lie on the correct boundaries\ndef test_boundaries(data_points):\n    t_values = data_points[:, 0]\n    x_values = data_points[:, 1]\n    assert np.all((t_values == 0) | (x_values == 1) | (x_values == -1)), "Some points do not lie on the correct boundaries."\n\ntest_boundaries(data_points)\nprint("Test 1 passed!")\n\n# Test 2: For t=0, label should be -sin(pi * x)\ndef test_labels_t_0(data_points, labels):\n    mask_t_0 = data_points[:, 0] == 0\n    expected_labels = -np.sin(np.pi * data_points[mask_t_0, 1])\n    assert np.allclose(labels[mask_t_0], expected_labels), "Labels for t=0 do not match -sin(pi * x)."\n\ntest_labels_t_0(data_points, labels)\nprint("Test 2 passed!")\n\n# Test 3: For x=-1 or x=1, label should be 0\ndef test_labels_x_boundaries(data_points, labels):\n    mask_x_boundaries = (data_points[:, 1] == 1) | (data_points[:, 1] == -1)\n    assert np.all(labels[mask_x_boundaries] == 0), "Labels for x=-1 or x=1 are not zero."\n\ntest_labels

In [187]:
num_points_t_0 = num_data_points

#create num_data_points random data points on the boundaries of the PDE
t_0_points = np.array( list(np.random.rand(num_points_t_0) - 1 ) )

t_0_labels = -np.sin(np.pi * t_0_points )

data_points, labels = t_0_points, t_0_labels

print(data_points, labels)


[-0.08828861 -0.54305412 -0.6049597  -0.26427295 -0.90715091 -0.42140752
 -0.34017648 -0.21002762 -0.18642413 -0.63923126 -0.04380153 -0.30231025
 -0.3852702  -0.42060471 -0.39697212 -0.35725043 -0.85253119 -0.89677197
 -0.6879362  -0.32004272 -0.28515921 -0.9020995  -0.43598434 -0.49295505
 -0.07130862 -0.41242662 -0.53277695 -0.37109151 -0.27942655 -0.37351056
 -0.26720809 -0.43970409 -0.17619228 -0.9896375  -0.71721514 -0.577119
 -0.37348865 -0.74737096 -0.24675117 -0.06950721 -0.25947639 -0.58775302
 -0.44833158 -0.03961368 -0.5548147  -0.20027666 -0.10002215 -0.22871733
 -0.02210835 -0.87049397 -0.22061138 -0.02108539 -0.64981254 -0.33087011
 -0.03738425 -0.39379249 -0.27568194 -0.21083958 -0.85394188 -0.10383583
 -0.03279923 -0.90353722 -0.13058199 -0.33806978 -0.26605042 -0.63708666
 -0.08045748 -0.97761311 -0.08691672 -0.21057172 -0.30583573 -0.30467407
 -0.35369337 -0.7379198  -0.40994539 -0.42746949 -0.19506118 -0.80267323
 -0.00129782 -0.93899682 -0.08513925 -0.4255014  -0.1

Preparing the Dataset and Dataloader

In [188]:
class PINN_DataSet(Dataset):
    def __init__(self, data, labels):
        self.data = data
        self.labels = labels

    def __len__(self):
        return len(self.data)

    def __getitem__(self, idx):
        return self.data[idx], self.labels[idx]

trainset = PINN_DataSet(data_points.astype(np.float32), labels.astype(np.float32)) #convert to float32, or else later the resulting torch tensors will be of torch.float64 type, which is not compatible with the neural network

batch_size = num_data_points #no mini-batches

num_workers = 0

trainloader = DataLoader(
    trainset,
    #batch_size = batch_size,
    shuffle = True,
    num_workers = num_workers
)



Defining the Neural Network

In [189]:
class PINN(nn.Module):
    def __init__(self):
        super().__init__()
        self.net = nn.Sequential( #9 layers of 20 neurons each
            nn.Linear(1,20),
            nn.Tanh(),
            nn.Linear(20,20),
            nn.Tanh(),
            nn.Linear(20,20),
            nn.Tanh(),
            nn.Linear(20,20),
            nn.Tanh(),
            nn.Linear(20,20),
            nn.Tanh(),
            nn.Linear(20,20),
            nn.Tanh(),
            nn.Linear(20,20),
            nn.Tanh(),
            nn.Linear(20,20),
            nn.Tanh(),
            nn.Linear(20,20),
            nn.Tanh(),
            nn.Linear(20,20),
            nn.Tanh(),
            nn.Linear(20,1),
            #nn.Tanh()

        )

    def forward(self, x):
        return self.net(x)



In [190]:

'''def init_weights(m):
    if type(m) == nn.Linear:
        nn.init.kaiming_normal_(m.weight, nonlinearity='relu')
        m.bias.data.fill_(0.01)


class PINN(nn.Module):
    def __init__(self):
        super().__init__()
        self.net = nn.Sequential( #9 layers of 20 neurons each
            nn.Linear(1,100),
            nn.ReLU(),
            nn.Linear(100,100),
            nn.ReLU(),
            nn.Linear(100,100),
            nn.ReLU(),
            nn.Linear(100,100),
            nn.ReLU(),
            nn.Linear(100,1)
        )
        self.net.apply(init_weights)

    def forward(self, x):
        return self.net(x)'''



"def init_weights(m):\n    if type(m) == nn.Linear:\n        nn.init.kaiming_normal_(m.weight, nonlinearity='relu')\n        m.bias.data.fill_(0.01)\n\n\nclass PINN(nn.Module):\n    def __init__(self):\n        super().__init__()\n        self.net = nn.Sequential( #9 layers of 20 neurons each\n            nn.Linear(1,100),\n            nn.ReLU(),\n            nn.Linear(100,100),\n            nn.ReLU(),\n            nn.Linear(100,100),\n            nn.ReLU(),\n            nn.Linear(100,100),\n            nn.ReLU(),\n            nn.Linear(100,1)\n        )\n        self.net.apply(init_weights)\n\n    def forward(self, x):\n        return self.net(x)"

Loss Function

In [191]:
  '''
def MSE_u(output, label):
    return torch.mean((output - label)**2)


def criterion(output, label, neural_network, device):
    #mse_u = nn.MSELoss()(output, label).squeeze()
    mse_u = MSE_u(output, label).squeeze()
    return  mse_u'''

'\ndef MSE_u(output, label):\n  return torch.mean((output - label)**2)\n\n\ndef criterion(output, label, neural_network, device):\n  #mse_u = nn.MSELoss()(output, label).squeeze()\n  mse_u = MSE_u(output, label).squeeze()\n  return  mse_u'

Model Training

In [192]:
'''pinn = PINN()
optimizer = torch.optim.LBFGS(pinn.parameters(), #PARAMETERS CREDIT TO https://github.com/teeratornk/PINNs-2/blob/master/Burgers%20Equation/Burgers%20Inference%20(PyTorch).ipynb
                              lr=1.0,
                              max_iter=50000, 
                                max_eval=50000, 
                                history_size=50,
                                tolerance_grad=1e-5, 
                                tolerance_change=1.0 * np.finfo(float).eps,
                                line_search_fn="strong_wolfe"
                              )



num_epochs = 50 #I have no idea how many epochs were used in the paper's implementation. Let's just do a lot for now and see how quickly training converges

#use the GPU to train if possible, else CPU
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print("Using device: " + ("GPU" if torch.cuda.is_available() else "CPU"))
pinn.to(device)

try:
    for epoch in range(num_epochs):

        print(f"EPOCH {epoch + 1} out of {num_epochs}")
        train_running_loss = 0


        for data in trainloader:

            input, label = data #input and label already seem to be tensors. Tbh, I am a little confused when this happened. I don't think I ever explicitly turned them into tensors. They used to both be numpy arrays. EDIT: Further research seems to show that dataloader does this automatically as it fetches data from the dataset
            input = input.to(device)
            label = label.to(device)


            def closure():
                optimizer.zero_grad() #reset the gradient so that the previous iteration does not affect the current one
                output = pinn(input) #run the batch through the current model
                loss = criterion(output, label, pinn, device) #calculate the loss
                loss.backward() #Using backpropagation, calculate the gradients
                print(f"Avg MSE Loss Per Boundary Data Point: {loss.item()}")
                return loss

            optimizer.step(closure) #Using the gradients, adjust the parameters    

except KeyboardInterrupt:
    print("Training interrupted by user.")  

print("TRAINING COMPLETE!")'''

'pinn = PINN()\noptimizer = torch.optim.LBFGS(pinn.parameters(), #PARAMETERS CREDIT TO https://github.com/teeratornk/PINNs-2/blob/master/Burgers%20Equation/Burgers%20Inference%20(PyTorch).ipynb\n                              lr=1.0,\n                              max_iter=50000, \n                                max_eval=50000, \n                                history_size=50,\n                                tolerance_grad=1e-5, \n                                tolerance_change=1.0 * np.finfo(float).eps,\n                                line_search_fn="strong_wolfe"\n                              )\n\n\n\nnum_epochs = 50 #I have no idea how many epochs were used in the paper\'s implementation. Let\'s just do a lot for now and see how quickly training converges\n\n#use the GPU to train if possible, else CPU\ndevice = torch.device("cuda" if torch.cuda.is_available() else "cpu")\nprint("Using device: " + ("GPU" if torch.cuda.is_available() else "CPU"))\npinn.to(device)\n\ntry:\n    for

In [193]:
pinn = PINN()


optimizer = torch.optim.Adam(pinn.parameters())
criterion = nn.MSELoss()


num_epochs = 500 #I have no idea how many epochs were used in the paper's implementation. Let's just do a lot for now and see how quickly training converges

#use the GPU to train if possible, else CPU
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print("Using device: " + ("GPU" if torch.cuda.is_available() else "CPU"))
pinn.to(device)

try:
    for epoch in range(num_epochs):

        print(f"EPOCH {epoch + 1} out of {num_epochs}")
        train_running_loss = 0


        for data in trainloader:

            input, label = data #input and label already seem to be tensors. Tbh, I am a little confused when this happened. I don't think I ever explicitly turned them into tensors. They used to both be numpy arrays. EDIT: Further research seems to show that dataloader does this automatically as it fetches data from the dataset
            input = input.to(device).view(-1,1)
            label = label.to(device)

            optimizer.zero_grad() #reset the gradient so that the previous iteration does not affect the current one
            output = pinn(input) #run the batch through the current model
            loss = criterion(output, label) #calculate the loss
            loss.backward() #Using backpropagation, calculate the gradients
            optimizer.step()
            print(f"Avg MSE Loss Per Boundary Data Point: {loss.item()}")
   

except KeyboardInterrupt:
    print("Training interrupted by user.")  

print("TRAINING COMPLETE!")

Using device: CPU
EPOCH 1 out of 500
Avg MSE Loss Per Boundary Data Point: 1.1533513069152832
Avg MSE Loss Per Boundary Data Point: 0.019470930099487305
Avg MSE Loss Per Boundary Data Point: 0.5582833886146545
Avg MSE Loss Per Boundary Data Point: 0.5898954272270203
Avg MSE Loss Per Boundary Data Point: 0.0007107898127287626
Avg MSE Loss Per Boundary Data Point: 0.8952543139457703
Avg MSE Loss Per Boundary Data Point: 0.8755619525909424
Avg MSE Loss Per Boundary Data Point: 0.7034007906913757
Avg MSE Loss Per Boundary Data Point: 0.0796019434928894
Avg MSE Loss Per Boundary Data Point: 0.7722172141075134
Avg MSE Loss Per Boundary Data Point: 0.18988780677318573
Avg MSE Loss Per Boundary Data Point: 0.6182771921157837
Avg MSE Loss Per Boundary Data Point: 0.6268020868301392
Avg MSE Loss Per Boundary Data Point: 0.0031108257826417685
Avg MSE Loss Per Boundary Data Point: 0.0006314541678875685
Avg MSE Loss Per Boundary Data Point: 0.05000293254852295
Avg MSE Loss Per Boundary Data Point: 

/Users/alexning/anaconda3/envs/env-1-ai/lib/python3.11/site-packages/torch/nn/modules/loss.py:536: UserWarning: Using a target size (torch.Size([1])) that is different to the input size (torch.Size([1, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Avg MSE Loss Per Boundary Data Point: 0.035969268530607224
Avg MSE Loss Per Boundary Data Point: 0.0037202932871878147
Avg MSE Loss Per Boundary Data Point: 0.04354240745306015
Avg MSE Loss Per Boundary Data Point: 1.2934882533954806e-06
Avg MSE Loss Per Boundary Data Point: 0.15606826543807983
Avg MSE Loss Per Boundary Data Point: 0.029879363253712654
Avg MSE Loss Per Boundary Data Point: 0.10343907028436661
Avg MSE Loss Per Boundary Data Point: 0.01471845805644989
Avg MSE Loss Per Boundary Data Point: 0.1279272884130478
Avg MSE Loss Per Boundary Data Point: 0.05745980143547058
Avg MSE Loss Per Boundary Data Point: 0.11964400857686996
Avg MSE Loss Per Boundary Data Point: 0.01979490928351879
Avg MSE Loss Per Boundary Data Point: 0.1303861141204834
Avg MSE Loss Per Boundary Data Point: 0.021190358325839043
Avg MSE Loss Per Boundary Data Point: 0.045043330639600754
Avg MSE Loss Per Boundary Data Point: 0.0036271666176617146
Avg MSE Loss Per Boundary Data Point: 0.005256775766611099
Avg 

Visual Plot